In [24]:
import pandas as pd
import folium
import utils

In [25]:
# Load the data
ListA = pd.read_csv('List A.csv')
ListB = pd.read_csv('List B.csv')
ListC = pd.read_csv('List C.csv')
ListD = pd.read_csv('List D.csv')

In [26]:
# Create three centroids, one in the North End, one in the Financial District, and one in the Back Bay
centroids = [[42.364506, -71.054733], [42.358894, -71.056742], [42.3505, -71.0760]]

northeastern_coordinate = "-71.09033,42.33976"

In [27]:
# Combine the two lists and add a column to indicate the list
ListA['list'] = 'A'
ListB['list'] = 'B'
ListC['list'] = 'C'
ListD['list'] = 'D'

TotalList = pd.concat([ListA, ListB, ListC, ListD])

In [28]:
# Remove all columns but name and gps
TotalList = TotalList[['name', 'gps', 'list']]

In [29]:
# Convert the gps column to a list of lists for k-means
TotalList['gps'] = TotalList['gps'].apply(lambda x: x.strip('[]').split(','))
TotalList['gps'] = TotalList['gps'].apply(lambda x: [float(i) for i in x])

In [30]:
# Create a new column with normalized gps coordinates and centroids
TotalList['normalized_gps'], norm_centroids = utils.normalize_gps(TotalList['gps'].values.tolist(), centroids)
display(TotalList)

name                        gps list  \
0   521 Commercial Street #525  [42.3688272, -71.0553792]    A   
1                     Acorn St  [42.3576234, -71.0688746]    A   
2    Arlington's Great Meadows  [42.4299758, -71.2038948]    A   
3        Arthur Fiedler Statue  [42.3565057, -71.0754527]    A   
4                     BU Beach  [42.3511927, -71.1060828]    A   
..                         ...                        ...  ...   
33               The Quiet Few  [42.3670906, -71.0359889]    D   
34        The Tall Ship Boston  [42.3649544, -71.0414523]    D   
35               Toasted Flats  [42.3711266, -71.0371343]    D   
36                 Vega Market   [42.3891835, -71.033703]    D   
37        Winthrop High School  [42.3803348, -70.9799864]    D   

                              normalized_gps  
0   [0.7251058917247415, 0.7797482353989729]  
1   [0.6747391031099019, 0.7451825969538083]  
2                  [1.0, 0.3993566550776867]  
3   [0.6697144722136962, 0.7283341725828262]  
4   [0.6458298305822171, 0.6498815915448888]  
..                                       ...  
33   [0.717298990038831, 0.8294124246148072]  
34  [0.7076956827824702, 0.8154190706511427]  
35  [0.7354428661210094, 0.8264787225922622]  
36  [0.8166178304491644, 0.8352672783369615]  
37   [0.7768384161061446, 0.972851090162032]  

[169 rows x 4 columns]

# 2 Routes

## Cluster and Minimize

In [31]:
# Cluster and minimize the data
norm_centroids_2 = norm_centroids[:2]
_, route_1_coordinates, route_2_coordinates = utils.cluster_and_minimize_2(TotalList, centroids, norm_centroids_2,
                                                                           northeastern_coordinate, 0.5, minimize=True)

/Users/garrinshieh/anaconda3/lib/python3.11/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/Users/garrinshieh/anaconda3/lib/python3.11/site-packages/sklearn/cluster/_kmeans.py:1412: RuntimeWarning: Explicit initial center position passed: performing only one init in KMeans instead of n_init=10.
  super()._check_params_vs_input(X, default_n_init=10)


## Create JSON

In [32]:
# Create a JSON request for the API
# This is the data we want to get from the API
route_1 = utils.list_to_string(route_1_coordinates)
route_2 = utils.list_to_string(route_2_coordinates)

In [33]:
# Create a dataframe from the JSON
df1 = utils.create_json_df(route_1, utils.list_to_string([centroids[0]]), northeastern_coordinate)
df2 = utils.create_json_df(route_2, utils.list_to_string([centroids[1]]), northeastern_coordinate)

In [34]:
# Add columns for the route number
df1['route'] = 1
df2['route'] = 2

# Concatenate the two dataframes
df = pd.concat([df1, df2], ignore_index=True)

In [35]:
display(df)

waypoint_index  trips_index  \
0                 0            0   
1                 1            0   
2                 2            0   
3                 3            0   
4                 4            0   
..              ...          ...   
168              64            0   
169              65            0   
170              66            0   
171              67            0   
172              68            0   

                                                  hint   distance  \
0    t4YsgAGHLIAAAAAAVQEAAAAAAAAwAAAAAAAAAHV0F0IAAA...  19.432511   
1    IzYEgGw1BIASAAAArwAAADMAAACUAwAAynkIQGUkmkEXlL...   6.024489   
2    G4gsgDiILICSAwAA5gAAAOkAAAAAAAAAQljLQnyXy0Fhy8...   2.602121   
3    gIosgLaKLIDOAAAArgAAAFwBAAAAAAAAp3O3QafxmUEQiR...  15.458439   
4    HpwsgCKcLIAAAAAAEgAAAAAAAAAAAAAAAAAAACg870AAAA...  39.201677   
..                                                 ...        ...   
168  cX8hgJF_IYA1AAAAMAAAAGcAAABOAAAATyWxQQ77nUEHMC...  22.776295   
169  g38hgI1_IYBOAAAAfwAAAAAAAAAAAAAAZ4ECQsbEUkIAAA...  12.789906   
170  e38hgIUAA4C6AgAAGQAAAAAAAAAAAAAA_DybQoNdJUEAAA...   6.310267   
171  k4chgBiIIYAKAAAAFwAAAPQDAAB_AgAAHn2aP-biHUBi6e...  36.240351   
172  DoUhgBeFIYCcAAAAJgAAAAAAAAARAAAAm0CKQdkZiEAAAA...   0.236958   

                       name                 location        lat        lon  \
0                            [-71.054865, 42.364361] -71.054865  42.364361   
1                            [-71.055569, 42.364032] -71.055569  42.364032   
2                            [-71.056164, 42.366918] -71.056164  42.366918   
3                            [-71.055561, 42.368861] -71.055561  42.368861   
4                            [-71.062507, 42.365968] -71.062507  42.365968   
..                      ...                      ...        ...        ...   
168        Alleghany Street   [-71.099348, 42.33047] -71.099348  42.330470   
169          Tremont Street  [-71.098267, 42.332009] -71.098267  42.332009   
170           Carmel Street  [-71.100092, 42.332401] -71.100092  42.332401   
171                          [-71.093834, 42.339096] -71.093834  42.339096   
172  Northeastern (Inbound)  [-71.090331, 42.339762] -71.090331  42.339762   

     route  
0        1  
1        1  
2        1  
3        1  
4        1  
..     ...  
168      2  
169      2  
170      2  
171      2  
172      2  

[173 rows x 9 columns]

## Map

In [36]:
# Create a map
m = folium.Map(location=[df['lon'].mean(), df['lat'].mean()], zoom_start=11)

# Add the points and lines for the two routes with different colors
colors = ['red', 'blue']

for route in df['route'].unique():
    df_route = df[df['route'] == route]
    folium.PolyLine(df_route[['lon', 'lat']].values.tolist(), color=colors[route - 1]).add_to(m)
    for i in range(len(df_route)):
        folium.CircleMarker(df_route[['lon', 'lat']].iloc[i].values.tolist(), radius=3, color=colors[route - 1]).add_to(
            m)

# Display the map
m

## Results

In [37]:
# Get the number of waypoints for each route
route_1_waypoints = len(route_1_coordinates)
route_2_waypoints = len(route_2_coordinates)
print("Route 1 has {} waypoints".format(route_1_waypoints))
print("Route 2 has {} waypoints".format(route_2_waypoints))

Route 1 has 102 waypoints
Route 2 has 67 waypoints


In [38]:
trip_hrs_1 = utils.get_trip_time(route_1, route_1_waypoints, utils.list_to_string([centroids[0]]),
                                 northeastern_coordinate)
print("The trip will take {} hours".format(trip_hrs_1))
trip_hrs_2 = utils.get_trip_time(route_2, route_2_waypoints, utils.list_to_string([centroids[1]]),
                                 northeastern_coordinate)
print("The trip will take {} hours".format(trip_hrs_2))

The trip will take 12.788333333333334 hours
The trip will take 13.1675 hours


# 3 Routes

In [47]:
# Cluster and minimize the data
_, route_1_coordinates, route_2_coordinates, route_3_coordinates = utils.cluster_and_minimize_3(TotalList, centroids,
                                                                                               norm_centroids,
                                                                                               northeastern_coordinate,
                                                                                               0.2, minimize=True)

/Users/garrinshieh/anaconda3/lib/python3.11/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)
/Users/garrinshieh/anaconda3/lib/python3.11/site-packages/sklearn/cluster/_kmeans.py:1412: RuntimeWarning: Explicit initial center position passed: performing only one init in KMeans instead of n_init=10.
  super()._check_params_vs_input(X, default_n_init=10)


## Create JSON

In [48]:
# Create a JSON request for the API
# This is the data we want to get from the API
route_1 = utils.list_to_string(route_1_coordinates)
route_2 = utils.list_to_string(route_2_coordinates)
route_3 = utils.list_to_string(route_3_coordinates)

In [49]:
# Create a dataframe from the JSON
df1 = utils.create_json_df(route_1, utils.list_to_string([centroids[0]]), northeastern_coordinate)
df2 = utils.create_json_df(route_2, utils.list_to_string([centroids[1]]), northeastern_coordinate)
df3 = utils.create_json_df(route_3, utils.list_to_string([centroids[2]]), northeastern_coordinate)

In [50]:
# Add columns for the route number
df1['route'] = 1
df2['route'] = 2
df3['route'] = 3

# Concatenate the three dataframes
df = pd.concat([df1, df2, df3], ignore_index=True)

In [51]:
display(df)

waypoint_index  trips_index  \
0                 0            0   
1                 1            0   
2                 2            0   
3                 3            0   
4                 4            0   
..              ...          ...   
170              29            0   
171              30            0   
172              31            0   
173              32            0   
174              33            0   

                                                  hint   distance  \
0    t4YsgAGHLIAAAAAAVQEAAAAAAAAwAAAAAAAAAHV0F0IAAA...  19.432511   
1    e1kugJlZLoBmAAAA6QAAAAAAAAAAAAAAZ6M2QSewzkEAAA...   4.756158   
2    tFkugHVaLoAOAAAAAAAAABgAAAAAAAAAwMG2QAAAAAB6ii...   4.525535   
3    sJAugLOQLoBuAQAAlAEAAAAAAAAAAAAAHFcjQvEZM0IAAA...   7.844897   
4    VREtgNlJBIBCAAAAYAAAAAAAAAARAAAAOOzeQU7vHkIAAA...  22.681980   
..                                                 ...        ...   
170  gLshgIS7IYAAAAAAPAAAAAAAAAAAAAAAAAAAAPGU1UAAAA...  10.782119   
171  e38hgIUAA4C6AgAAGQAAAAAAAAAAAAAA_DybQoNdJUEAAA...   6.310267   
172  cX8hgJF_IYA1AAAAMAAAAGcAAABOAAAATyWxQQ77nUEHMC...  22.776295   
173  s9QhgLbUIYAwAAAAkAAAAAAAAAAAAAAA2XmpQNgrgEEAAA...   4.111715   
174  DoUhgBeFIYCcAAAAJgAAAAAAAAARAAAAm0CKQdkZiEAAAA...   0.236958   

                       name                 location        lat        lon  \
0                            [-71.054865, 42.364361] -71.054865  42.364361   
1                            [-71.060933, 42.376178] -71.060933  42.376178   
2                            [-71.060753, 42.376391] -71.060753  42.376391   
3                            [-71.060948, 42.380436] -71.060948  42.380436   
4            Factory Street  [-71.061206, 42.398809] -71.061206  42.398809   
..                      ...                      ...        ...        ...   
170                           [-71.10963, 42.336448] -71.109630  42.336448   
171           Carmel Street  [-71.100092, 42.332401] -71.100092  42.332401   
172        Alleghany Street   [-71.099348, 42.33047] -71.099348  42.330470   
173                           [-71.09454, 42.325354] -71.094540  42.325354   
174  Northeastern (Inbound)  [-71.090331, 42.339762] -71.090331  42.339762   

     route  
0        1  
1        1  
2        1  
3        1  
4        1  
..     ...  
170      3  
171      3  
172      3  
173      3  
174      3  

[175 rows x 9 columns]

## Map

In [52]:
# Create a map
m = folium.Map(location=[df['lon'].mean(), df['lat'].mean()], zoom_start=11)

# Add the points and lines for the three routes with different colors
colors = ['red', 'blue', 'green']

for route in df['route'].unique():
    df_route = df[df['route'] == route]
    folium.PolyLine(df_route[['lon', 'lat']].values.tolist(), color=colors[route - 1]).add_to(m)
    for i in range(len(df_route)):
        folium.CircleMarker(df_route[['lon', 'lat']].iloc[i].values.tolist(), radius=3, color=colors[route - 1]).add_to(
            m)
        
# Display the map
m

## Results

In [53]:
# Get the number of waypoints for each route
route_1_waypoints = len(route_1_coordinates)
route_2_waypoints = len(route_2_coordinates)
route_3_waypoints = len(route_3_coordinates)
print("Route 1 has {} waypoints".format(route_1_waypoints))
print("Route 2 has {} waypoints".format(route_2_waypoints))
print("Route 3 has {} waypoints".format(route_3_waypoints))

Route 1 has 57 waypoints
Route 2 has 80 waypoints
Route 3 has 32 waypoints


In [54]:
# Get the trip time for each route
trip_hrs_1 = utils.get_trip_time(route_1, route_1_waypoints, utils.list_to_string([centroids[0]]),
                                 northeastern_coordinate)
print("The trip will take {} hours".format(trip_hrs_1))
trip_hrs_2 = utils.get_trip_time(route_2, route_2_waypoints, utils.list_to_string([centroids[1]]),
                                 northeastern_coordinate)
print("The trip will take {} hours".format(trip_hrs_2))
trip_hrs_3 = utils.get_trip_time(route_3, route_3_waypoints, utils.list_to_string([centroids[2]]),
                                 northeastern_coordinate)
print("The trip will take {} hours".format(trip_hrs_3))

The trip will take 9.175 hours
The trip will take 9.341111111111111 hours
The trip will take 9.398333333333333 hours
